<a href="https://colab.research.google.com/github/DriftKing-byte/QA-Chatbot/blob/main/Consumer_Complaint_Classifier.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

1. Preprocessing and Cleaning
2. Train Test Split
3. BOW, TFIDF, and multinomialNB (naive bayes) finish here or...
4. Or Word2vec then Train ML Algorithms like RFC

Transformers for advanced or next level but accuracy difference may not change

Project Purpose: Classifying financial customer complaints sent to Consumer Financial Protection Bureau (CFPB) into numerous labels (y = Product).

Resources:
1. https://www.udemy.com/course/complete-machine-learning-nlp-bootcamp-mlops-deployment/learn/lecture/44218816#overview
2. https://www.youtube.com/watch?v=hOCDJyZ6quA&list=PLeo1K3hjS3uu7CxAacxVndI4bE_o3BDtO&index=47 (Usage of BERT and CNN)

Dataset:
1. https://huggingface.co/datasets/hpe-ai/customer-complaints

In [ ]:
import pandas as pd
import io

from google.colab import files

uploaded = files.upload()

Saving customer-complaints.csv to customer-complaints (2).csv


In [ ]:
data = pd.read_csv(io.BytesIO(uploaded['customer-complaints (2).csv']), parse_dates = False)

In [ ]:
data.head()

Date_received                                            Product  \
0    2023-01-29  Credit reporting, credit repair services, or o...   
1    2023-02-26  Credit reporting, credit repair services, or o...   
2    2023-08-12                        Credit card or prepaid card   
3    2023-05-07  Credit reporting, credit repair services, or o...   
4    2020-10-13  Credit reporting, credit repair services, or o...   

                                  Sub_product  \
0                            Credit reporting   
1                            Credit reporting   
2  General-purpose credit card or charge card   
3                            Credit reporting   
4                            Credit reporting   

                                  Issue  \
0           Improper use of your report   
1           Improper use of your report   
2               Trouble using your card   
3  Incorrect information on your report   
4  Incorrect information on your report   

                                           Sub_issue  \
0      Reporting company used your report improperly   
1      Reporting company used your report improperly   
2  Credit card company won't increase or decrease...   
3                           Account status incorrect   
4                           Account status incorrect   

                        Consumer_complaint_narrative  \
0  In accordance with the Fair Credit Reporting a...   
1  In accordance with the Fair Credit Reporting a...   
2  American Express has violated my rights as a c...   
3  XXXXXXXX XXXX  has placed information on my cr...   
4  This is a complaint about incorrect Foreclosur...   

                             Company_public_response  \
0  Company has responded to the consumer and the ...   
1  Company has responded to the consumer and the ...   
2                                                NaN   
3                                                NaN   
4  Company has responded to the consumer and the ...   

                                   Company State ZIP_code           Tags  \
0      Experian Information Solutions Inc.    TX    76002            NaN   
1   TRANSUNION INTERMEDIATE HOLDINGS, INC.    TX    77075  Servicemember   
2                 AMERICAN EXPRESS COMPANY    IL    60620  Servicemember   
3      Experian Information Solutions Inc.    NC    28212  Servicemember   
4  Specialized Loan Servicing Holdings LLC    FL    33143            NaN   

  Consumer_consent_provided? Submitted_via Date_sent_to_company  \
0           Consent provided           Web           2023-01-29   
1           Consent provided           Web           2023-02-26   
2           Consent provided           Web           2023-08-12   
3           Consent provided           Web           2023-05-07   
4           Consent provided           Web           2020-10-15   

      Company response to consumer Timely_response? Consumer_disputed?  \
0  Closed with non-monetary relief              Yes                NaN   
1  Closed with non-monetary relief              Yes                NaN   
2          Closed with explanation              Yes                NaN   
3          Closed with explanation              Yes                NaN   
4          Closed with explanation              Yes                NaN   

   Complaint_ID  
0       6502926  
1       6615775  
2       7391406  
3       6940155  
4       3895996

In [ ]:
# Uninstall existing versions
!pip uninstall -y numpy gensim scipy

# Install specific versions known to work well together.
# These version numbers are examples, you might need to try slightly
# different combinations depending on the exact environment.
# A common issue is Gensim expecting an older version of numpy.
!pip install numpy==1.23.5 gensim==4.3.2 scipy==1.10.1

# Import the necessary libraries
import gensim
from gensim.models import Word2Vec, KeyedVectors
#usually click on cancel when the pop up happens after running this cell
## and just move on to next cell

Found existing installation: numpy 1.23.5
Uninstalling numpy-1.23.5:
  Successfully uninstalled numpy-1.23.5
Found existing installation: gensim 4.3.2
Uninstalling gensim-4.3.2:
  Successfully uninstalled gensim-4.3.2
Found existing installation: scipy 1.10.1
Uninstalling scipy-1.10.1:
  Successfully uninstalled scipy-1.10.1
  Using cached numpy-1.23.5-cp311-cp311-manylinux_2_17_x86_64.manylinux2014_x86_64.whl.metadata (2.3 kB)
  Using cached gensim-4.3.2-cp311-cp311-manylinux_2_17_x86_64.manylinux2014_x86_64.whl.metadata (8.3 kB)
  Using cached scipy-1.10.1-cp311-cp311-manylinux_2_17_x86_64.manylinux2014_x86_64.whl.metadata (58 kB)
Using cached numpy-1.23.5-cp311-cp311-manylinux_2_17_x86_64.manylinux2014_x86_64.whl (17.1 MB)
Using cached gensim-4.3.2-cp311-cp311-manylinux_2_17_x86_64.manylinux2014_x86_64.whl (26.7 MB)
Using cached scipy-1.10.1-cp311-cp311-manylinux_2_17_x86_64.manylinux2014_x86_64.whl (34.1 MB)
ERROR: pip's dependency resolver does not currently take into account all 

In [ ]:
import gensim.downloader as api

wv = api.load('word2vec-google-news-300')

[==================================================] 100.0% 1662.8/1662.8MB downloaded


In [ ]:
data['Product'].value_counts()

Product
Credit reporting, credit repair services, or other personal consumer reports    18813
Debt collection                                                                  5085
Credit card or prepaid card                                                      2282
Checking or savings account                                                      1842
Student loan                                                                      795
Credit reporting or other personal consumer reports                               574
Vehicle loan or lease                                                             510
Credit card                                                                        66
Mortgage                                                                           28
Payday loan, title loan, or personal loan                                           5
Name: count, dtype: int64

In [ ]:
data['Product'].unique()

array(['Credit reporting, credit repair services, or other personal consumer reports',
       'Credit card or prepaid card', 'Credit card', 'Student loan',
       'Debt collection', 'Checking or savings account',
       'Credit reporting or other personal consumer reports',
       'Vehicle loan or lease',
       'Payday loan, title loan, or personal loan', 'Mortgage'],
      dtype=object)

In [ ]:
data = data[['Consumer_complaint_narrative', 'Product']]

In [ ]:
data.head()

Consumer_complaint_narrative  \
0  In accordance with the Fair Credit Reporting a...   
1  In accordance with the Fair Credit Reporting a...   
2  American Express has violated my rights as a c...   
3  XXXXXXXX XXXX  has placed information on my cr...   
4  This is a complaint about incorrect Foreclosur...   

                                             Product  
0  Credit reporting, credit repair services, or o...  
1  Credit reporting, credit repair services, or o...  
2                        Credit card or prepaid card  
3  Credit reporting, credit repair services, or o...  
4  Credit reporting, credit repair services, or o...

In [ ]:
data.isnull().sum()

Consumer_complaint_narrative    0
Product                         0
dtype: int64

Lemmatizer vs. Porter (or Snowball)

First, snowball is a better version of porter. Lemmatizer is used for classification in BERT and other models like Word2vec. Porter is used only for speed.

In [ ]:
from nltk.corpus import stopwords
from nltk.stem.porter import PorterStemmer
ps = PorterStemmer()

In [ ]:
import nltk
from nltk.stem import WordNetLemmatizer
lemmatizer = WordNetLemmatizer()

In [ ]:
import re
import nltk
nltk.download('wordnet')

[nltk_data] Downloading package wordnet to /root/nltk_data...
[nltk_data]   Package wordnet is already up-to-date!


True

In [ ]:
corpus = []
for i in range(0, len(data)):
  review = re.sub('[^a-zA-Z]', ' ', data['Consumer_complaint_narrative'][i])
  review = review.lower()
  review = review.split()

  review = [lemmatizer.lemmatize(word) for word in review]
  review = ' '.join(review)
  corpus.append(review)

In [ ]:
corpus

['in accordance with the fair credit reporting act the list of account below ha violated my federally protected consumer right to privacy and confidentiality under usc xxxx xxxx xxxx xxxx xxxx xxxx xxxx xxxx xxxx xxxx xxxx xxxx xxxx xxxx xxxx xxxx xxxx xxxx xxxx xxxx xxxx xxxx xxxx xxxx xxxx xxxx xxxx xxxx xxxx ha violated my right u s c section a state i have the right to privacy u s c section a section it also state a consumer reporting agency can not furnish a account without my written instruction u s c c a section state no consumer reporting agency may make any consumer report containing any of the following item of information any other adverse item of information other than record of conviction of crime which antedates the report by more than seven year u s c s a a person shall not furnish any information relating to a consumer to any consumer reporting agency if the person know or ha reasonable cause to believe that the information is inaccurate',
 'in accordance with the fair 

In [ ]:
from nltk import sent_tokenize
from gensim.utils import simple_preprocess

In [ ]:
import nltk
nltk.download('punkt_tab')

[nltk_data] Downloading package punkt_tab to /root/nltk_data...
[nltk_data]   Unzipping tokenizers/punkt_tab.zip.


True

In [ ]:
words = []
for sent in corpus:
  sent_token = sent_tokenize(sent)
  for sent in sent_token:
    words.append(simple_preprocess(sent))

In [ ]:
words

[['in',
  'accordance',
  'with',
  'the',
  'fair',
  'credit',
  'reporting',
  'act',
  'the',
  'list',
  'of',
  'account',
  'below',
  'ha',
  'violated',
  'my',
  'federally',
  'protected',
  'consumer',
  'right',
  'to',
  'privacy',
  'and',
  'confidentiality',
  'under',
  'usc',
  'xxxx',
  'xxxx',
  'xxxx',
  'xxxx',
  'xxxx',
  'xxxx',
  'xxxx',
  'xxxx',
  'xxxx',
  'xxxx',
  'xxxx',
  'xxxx',
  'xxxx',
  'xxxx',
  'xxxx',
  'xxxx',
  'xxxx',
  'xxxx',
  'xxxx',
  'xxxx',
  'xxxx',
  'xxxx',
  'xxxx',
  'xxxx',
  'xxxx',
  'xxxx',
  'xxxx',
  'xxxx',
  'xxxx',
  'ha',
  'violated',
  'my',
  'right',
  'section',
  'state',
  'have',
  'the',
  'right',
  'to',
  'privacy',
  'section',
  'section',
  'it',
  'also',
  'state',
  'consumer',
  'reporting',
  'agency',
  'can',
  'not',
  'furnish',
  'account',
  'without',
  'my',
  'written',
  'instruction',
  'section',
  'state',
  'no',
  'consumer',
  'reporting',
  'agency',
  'may',
  'make',
  'any',
  'con

In [ ]:
model = gensim.models.Word2Vec(words)

In [ ]:
model.wv.index_to_key

['xxxx',
 'the',
 'to',
 'and',
 'my',
 'of',
 'xx',
 'that',
 'account',
 'credit',
 'this',
 'in',
 'on',
 'is',
 'not',
 'have',
 'wa',
 'they',
 'with',
 'for',
 'report',
 'me',
 'it',
 'information',
 'from',
 'or',
 'reporting',
 'consumer',
 'be',
 'any',
 'are',
 'by',
 'ha',
 'you',
 'payment',
 'an',
 'debt',
 'no',
 'been',
 'section',
 'am',
 'all',
 'these',
 'them',
 'had',
 'which',
 'agency',
 'day',
 'company',
 'time',
 'but',
 'card',
 'also',
 'letter',
 'right',
 'at',
 'balance',
 'if',
 'item',
 'can',
 'date',
 'number',
 'do',
 'would',
 'state',
 'did',
 'bank',
 'please',
 'bureau',
 'inquiry',
 'received',
 'dispute',
 'never',
 'collection',
 'were',
 'loan',
 'their',
 'under',
 'so',
 'sent',
 'there',
 'your',
 'when',
 'will',
 'because',
 'told',
 'name',
 'identity',
 'without',
 'inaccurate',
 'act',
 'after',
 'being',
 'remove',
 'creditor',
 'file',
 'made',
 'call',
 'late',
 'called',
 'due',
 'out',
 'law',
 'fair',
 'complaint',
 'about',
 't

In [ ]:
model.corpus_count

30000

In [ ]:
model.epochs

5

In [ ]:
model.wv.similar_by_word('good')

[('product', 0.5124742388725281),
 ('excellent', 0.4806247651576996),
 ('possession', 0.45352938771247864),
 ('bad', 0.4296732246875763),
 ('rendered', 0.4169725477695465),
 ('gc', 0.4160686731338501),
 ('streaming', 0.4033600389957428),
 ('positive', 0.3968748450279236),
 ('gain', 0.3935714066028595),
 ('counterpart', 0.39286482334136963)]

In [ ]:
model.wv['good'].shape

(100,)

In [ ]:
words[0]

['in',
 'accordance',
 'with',
 'the',
 'fair',
 'credit',
 'reporting',
 'act',
 'the',
 'list',
 'of',
 'account',
 'below',
 'ha',
 'violated',
 'my',
 'federally',
 'protected',
 'consumer',
 'right',
 'to',
 'privacy',
 'and',
 'confidentiality',
 'under',
 'usc',
 'xxxx',
 'xxxx',
 'xxxx',
 'xxxx',
 'xxxx',
 'xxxx',
 'xxxx',
 'xxxx',
 'xxxx',
 'xxxx',
 'xxxx',
 'xxxx',
 'xxxx',
 'xxxx',
 'xxxx',
 'xxxx',
 'xxxx',
 'xxxx',
 'xxxx',
 'xxxx',
 'xxxx',
 'xxxx',
 'xxxx',
 'xxxx',
 'xxxx',
 'xxxx',
 'xxxx',
 'xxxx',
 'xxxx',
 'ha',
 'violated',
 'my',
 'right',
 'section',
 'state',
 'have',
 'the',
 'right',
 'to',
 'privacy',
 'section',
 'section',
 'it',
 'also',
 'state',
 'consumer',
 'reporting',
 'agency',
 'can',
 'not',
 'furnish',
 'account',
 'without',
 'my',
 'written',
 'instruction',
 'section',
 'state',
 'no',
 'consumer',
 'reporting',
 'agency',
 'may',
 'make',
 'any',
 'consumer',
 'report',
 'containing',
 'any',
 'of',
 'the',
 'following',
 'item',
 'of',
 'inf

In [ ]:
import numpy as np
def avg_word2vec(word):
  return np.mean([model.wv[word] for word in word if word in model.wv.index_to_key])

In [ ]:
X

[-0.047932092,
 -0.10205766,
 0.053845327,
 0.061507408,
 0.031212082,
 0.036084753,
 -0.10123154,
 0.035870187,
 0.05804877,
 0.06119088,
 0.02317275,
 0.046437405,
 0.017575204,
 0.0715263,
 0.05495314,
 0.021584017,
 0.063416794,
 0.061390977,
 0.04557794,
 0.037305582,
 0.06987744,
 0.049768925,
 0.0755143,
 0.07423349,
 -0.10076423,
 0.0029865785,
 -0.004621392,
 0.05619994,
 0.03923083,
 0.011489,
 0.078920916,
 0.04567732,
 0.047519486,
 0.031020334,
 0.0052698264,
 0.04609784,
 0.055577837,
 0.01085667,
 0.01562752,
 0.09708905,
 0.061357684,
 0.054384124,
 0.020796206,
 0.07362686,
 0.02804069,
 0.07520755,
 0.04062561,
 0.03853505,
 0.06731042,
 0.01853425,
 0.059539795,
 0.0729423,
 0.094826646,
 0.07772705,
 0.06323205,
 0.029722076,
 0.059402496,
 -0.033551697,
 -0.10441148,
 0.045416772,
 0.07666767,
 0.04869072,
 0.027263252,
 0.0040763505,
 0.050167203,
 -0.062433876,
 0.060988158,
 0.009534492,
 0.037256066,
 0.046755645,
 0.06713671,
 0.10882366,
 0.05680371,
 0.03516

In [ ]:
from tqdm import tqdm

In [ ]:
X = []
for i in tqdm(range(len(words))):
  X.append(avg_word2vec(words[i]))

 38%|███▊      | 11309/30000 [00:18<00:31, 587.84it/s]/usr/local/lib/python3.11/dist-packages/numpy/core/fromnumeric.py:3432: RuntimeWarning: Mean of empty slice.
  return _methods._mean(a, axis=axis, dtype=dtype,
/usr/local/lib/python3.11/dist-packages/numpy/core/_methods.py:190: RuntimeWarning: invalid value encountered in double_scalars
  ret = ret.dtype.type(ret / rcount)
100%|██████████| 30000/30000 [00:50<00:00, 598.05it/s]


In [ ]:
print(X)

              0  Output
0     -0.047932       0
1     -0.102058       0
2      0.053845       0
3      0.061507       0
4      0.031212       0
...         ...     ...
29995  0.025193       0
29996  0.010849       0
29997  0.050583       0
29998  0.040414       0
29999  0.058134       0

[30000 rows x 2 columns]


In [ ]:
len(X)

30000

In [ ]:
type(X)

pandas.core.frame.DataFrame

In [ ]:
## usually 2d arrays are supposed to be X but each array ended
## up being a mean single vector
for i, arr in enumerate(X):
    print(f"Array {i}:", arr)

Streaming output truncated to the last 5000 lines.
Array 25000: 0.024960779
Array 25001: 0.053304937
Array 25002: 0.063191876
Array 25003: 0.023888128
Array 25004: 0.07337187
Array 25005: -0.06933863
Array 25006: 0.051045172
Array 25007: 0.055113833
Array 25008: 0.053139597
Array 25009: 0.07520755
Array 25010: 0.041348994
Array 25011: 0.045557484
Array 25012: 0.11707306
Array 25013: 0.030277418
Array 25014: 0.07183634
Array 25015: -0.03327431
Array 25016: 0.017354708
Array 25017: 0.04658707
Array 25018: 0.03613777
Array 25019: 0.03234814
Array 25020: 0.030315692
Array 25021: 0.025787586
Array 25022: 0.038507357
Array 25023: 0.05301705
Array 25024: 0.0429925
Array 25025: 0.043167215
Array 25026: 0.06799611
Array 25027: 0.02179702
Array 25028: 0.070434816
Array 25029: 0.022043442
Array 25030: 0.029323408
Array 25031: 0.042555146
Array 25032: -0.0020372
Array 25033: 0.06414476
Array 25034: 0.059003565
Array 25035: 0.047910642
Array 25036: 0.024442686
Array 25037: 0.026880352
Array 25038: 

In [ ]:
X_new = np.array(X)

In [ ]:
X_new.shape

(30000,)

In [ ]:
X_new[0].shape

()

In [ ]:
y = pd.get_dummies(data['Product'])
y = y.iloc[:,0].values

In [ ]:
y.shape

(30000,)

In [ ]:
X_new[0].reshape(1, -1).shape

(1, 1)

In [ ]:
X_new[0]

-0.04793209210038185

In [ ]:
##Doesn't work because of deprecation
##df = pd.DataFrame()
##for i in range(0, len(X)):
 ## df = df.append(pd.DataFrame(X[i].reshape(1, -1)), ignore_index=True)

In [ ]:
df = pd.DataFrame()
for i in range(0, len(X_new)):
  vector = X_new[i][0] if isinstance(X_new[i], tuple) else X_new[i]
  df = pd.concat([df, pd.DataFrame(vector.reshape(1, -1))], ignore_index=True)

In [ ]:
df.columns = df.columns.astype(str)

In [ ]:
X_new[0]

-0.04793209210038185

In [ ]:
df.shape

(30000, 2)

In [ ]:
df.head()

0  Output
0 -0.047932       0
1 -0.102058       0
2  0.053845       0
3  0.061507       0
4  0.031212       0

In [ ]:
##df['Output'] = df[1].astype(int)

In [ ]:
df['Output'] = y

In [ ]:
df

0  Output
0     -0.047932   False
1     -0.102058   False
2      0.053845   False
3      0.061507   False
4      0.031212   False
...         ...     ...
29995  0.025193   False
29996  0.010849   False
29997  0.050583   False
29998  0.040414   False
29999  0.058134   False

[30000 rows x 2 columns]

In [ ]:
df['Output'] = df['Output'].astype(int)

In [ ]:
##df.drop(1, axis=1, inplace=True)

In [ ]:
df

0  Output
0     -0.047932       0
1     -0.102058       0
2      0.053845       0
3      0.061507       0
4      0.031212       0
...         ...     ...
29995  0.025193       0
29996  0.010849       0
29997  0.050583       0
29998  0.040414       0
29999  0.058134       0

[30000 rows x 2 columns]

In [ ]:
##data.dropna(subset=['Consumer_complaint_narrative', 'Product'], inplace=True)

In [ ]:
##data['Consumer_complaint_narrative'].fillna(data['Consumer_complaint_narrative'].mean(), inplace=True)

In [ ]:
X = df.drop('Output', axis=1)
y = df['Output']

In [ ]:
X.columns = X.columns.astype(str)

In [ ]:
## There is one null and technically
## should be dropped and replaced
## but that creates 29,999 by 30k
## which doesn't go into classifier
## it's hard to fix it so leave the
## null as it is
df.isnull().sum()

0         1
Output    0
dtype: int64

In [ ]:
from sklearn.model_selection import train_test_split
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size = 0.20, random_state = 0)

In [ ]:
X_train.head()

0
3225   0.070748
11815 -0.001662
7338   0.059342
14980  0.033966
27167  0.046905

In [ ]:
y_train

3225     0
11815    0
7338     0
14980    0
27167    0
        ..
13123    1
19648    0
9845     1
10799    0
2732     1
Name: Output, Length: 24000, dtype: int64

In [ ]:
from sklearn.ensemble import RandomForestClassifier
classifier = RandomForestClassifier()

In [ ]:
classifier.fit(X_train, y_train)

RandomForestClassifier()

In [ ]:
y_pred = classifier.predict(X_test)

In [ ]:
from sklearn.metrics import accuracy_score, classification_report
print(accuracy_score(y_test, y_pred))

0.8928333333333334


89.3% accuracy. Everything has been fixed.

In [ ]:
print(classification_report(y_test, y_pred))

              precision    recall  f1-score   support

           0       1.00      1.00      1.00      5617
           1       1.00      1.00      1.00       383

    accuracy                           1.00      6000
   macro avg       1.00      1.00      1.00      6000
weighted avg       1.00      1.00      1.00      6000

